In [2]:
import sys
sys.path.insert(1, '/scratch/cinthiasouza/mv-text-summarizer')

import itertools
import re

import glob, os
import pandas as pd
import json
import spacy
import nltk
import numpy as np
import json
#import seaborn as sns
import pickle

#from bs4 import BeautifulSoup
#from pysbd.utils import PySBDFactory
import math

#from sumeval.metrics.rouge import RougeCalculator
#rouge = RougeCalculator(stopwords=True, lang="en")
#import matplotlib.pyplot as plt
import random
#from collections import Counter

from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report
from sklearn.preprocessing import StandardScaler
#from timeit import default_timer as timer 
#from imblearn.over_sampling import SMOTE
#from sklearn.metrics import matthews_corrcoef
#from imblearn.under_sampling import RandomUnderSampler
#from imblearn.pipeline import Pipeline
#from sklearn.model_selection import cross_val_score
#from sklearn.ensemble import RandomForestClassifier
#from sklearn.ensemble import GradientBoostingClassifier
#from sklearn.neighbors import KNeighborsClassifier
#from sklearn.svm import SVC
#from sklearn.ensemble import AdaBoostClassifier
#from catboost import CatBoostClassifier
#from tensorflow.keras.models import model_from_json

#nltk.download('averaged_perceptron_tagger')
#nltk.download('maxent_ne_chunker')
#nltk.download('words')
#nltk.download('punkt')
#nltk.download('stopwords')

#!python -m spacy download en_core_web_sm
#nlp_sm = spacy.load('en_core_web_sm')

import en_core_web_sm
nlp_md = en_core_web_sm.load()

import en_core_web_md
nlp_md = en_core_web_md.load()
#!python -m spacy download en_core_web_md
#nlp_md = spacy.load('en_core_web_md')

import warnings
warnings.filterwarnings("ignore")

path_base = "/scratch/cinthiasouza/mv-text-summarizer"
path_to_read="/scratch/cinthiasouza/mv-text-summarizer/result/{}/{}_*.csv"

In [3]:
%load_ext autoreload
%autoreload 2

from src import preprocess
from src import extract_features
from src import tokenizer
from src import create_features_df
from src import transform_data
from src import loader
from src import utils
from src import ensemble_tree_models
from src import tunning_hyperparametrs as th
#from src import mlp_regressor
#from src import mlp_classifier
from src import summarization
from src import normalization
from src import ensemble_tree_models as classifiers
from src import utils_classification as utils_clf
from src import evaluate_classifiers as ev
from src import prepare_data
from src import display_results as dr
import joblib
from joblib import Parallel, delayed
#from tensorflow.keras.utils import to_categorical
from src import pipeline_extract_features as pef

In [4]:
print("oi")

oi


In [5]:
from tensorflow import keras
from tensorflow.keras.models import model_from_json
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.metrics import Precision

In [6]:
def load_keras_model(path_to_save, name_model, section):

    json_file = open('{}/{}_{}.json'.format(path_to_save, name_model, section), 'r')
    model = json_file.read()
    json_file.close()
    model = model_from_json(model)
    model.load_weights('{}/{}_{}.h5'.format(path_to_save, name_model, section))
    print("Loaded model from disk")
    model.compile(loss='categorical_crossentropy', optimizer=keras.optimizers.Adam(
                            learning_rate=0.001), metrics=[keras.metrics.Precision()])
    
    return model

In [7]:
def load_classifiers(sections, path_to_read, name_models):

    models = {}
    
    for section in sections:
        
        aux = {}
        
        for name_model in name_models:
            if name_model != 'mlp':
                aux[name_model] = joblib.load('{}/{}_{}.pkl'.format(path_to_read, name_model,  section))
            elif (name_model == 'mlp') or (name_model == 'embed_mlp') or (name_model == 'mv_mlp_bert') :
                aux[name_model] = load_keras_model(section, path_to_read)
            
        models[section] = aux
        
    return models

In [8]:
def remove_ascii(text):
    
    try:
        return re.sub(r'[^\x00-\x7F]+', '', text)
    except:
        return " "

In [9]:
def pipeline_summarization(
    features, scores, references, predictions, section, name_models,
    summ_items, k=3, sort_scores=True, proba=False, ascending=False):
    
    X_test = features
    y_test = scores
    
    vfunc = np.vectorize(remove_ascii)
    X_test['sentences'] = vfunc(X_test['sentences'])

    df_proba = summarization.create_df(name_models, X_test, y_test['rouge_1'], predictions, section, proba=proba)
    
    if proba:
        df = summarization.binarize_proba(df_proba.copy(), name_models, k, sort_scores, ascending)
    else:
        df = df_proba.copy()
        
    summaries = summarization.create_summaries(df, references, summ_items, name_models)
    result = summarization.evaluate_summaries(summaries, name_models)
    
    return df_proba, df, summaries, result

In [10]:
def create_df_v2(name_models, x_summ):
    
    df = pd.DataFrame({'sentences': x_summ['sentences'],
                       'rouge_1': list(x_summ['rouge_1']),
                       'articles': x_summ['articles']})
    
    for name_model in name_models:
            df[name_model] = list(x_summ['rouge_1'])
            
    return df

In [11]:
def summarization_target(
    df, references, name_models, summ_items, sort_scores=False, proba=False, ascending=False):
    
    df = create_df_v2(name_models, df.copy())

    df = summarization.binarize_proba(df.copy(), name_models, 3, sort_scores, ascending)

    summaries = summarization.create_summaries(df, references, summ_items, name_models)
    result = summarization.evaluate_summaries(summaries, name_models)
    
    return df, summaries, result

In [12]:
def load_predict_models(dataset, sections, name_models, columns, path_to_save, embed_path,  index_Xtest):
     
    predictions_proba = {}
    models = {}

    for section in sections:

        aux = {}
        aux_models = {}
        
        X_test_embed = pd.read_csv("dataset/{}_{}_test.csv".format(embed_path, section))
        X_test_embed = X_test_embed[columns]
        
        X_test_features = dataset[section][index_Xtest]
        
        for name_model in name_models:

            #Load
            if (name_model != 'mlp') and (name_model != 'mlp_embed') and (name_model != 'mv_mlp_bert'):
                model = joblib.load('{}/{}_{}.pkl'.format(path_to_save, name_model, section))
            else :
                model = load_keras_model(path_to_save, name_model, section)

            #predict
            if (name_model == 'mv_mlp_bert') or (name_model == 'mv_mlp'):
                y_pred = model.predict([X_test_embed, X_test_features])
            elif name_model == "mlp":
                y_pred = model.predict(X_test_features)
            elif name_model == 'mlp_embed':
                y_pred = model.predict(X_test_embed)
            else:
                y_pred = model.predict_proba(X_test_features)


            aux[name_model] = y_pred
            aux_models[name_model] = model

        predictions_proba[section]= aux
        models[section] = aux_models
        
    return predictions_proba, models

In [18]:
with open('dataset/dataset_{}.pkl'.format('features'), 'rb') as fp:
    dataset = pickle.load(fp)
    
columns_name = ['text_rank', 'lex_rank', 'count_one_gram', 'count_one_gram', 'count_one_gram',
        'count_article_keywords',
       'tf-isf', 'position_score', 'paragraph_score',
       'length_score', 'pos_score', 'ner_score', 'dist_centroid']

sections=['introduction', 'materials', 'conclusion']

path_to_save = "/scratch/cinthiasouza/mv-text-summarizer/notebook/models_features_weights"

In [25]:
dataset['introduction'][0].shape

(96246, 13)

In [26]:
path_to_save = "/scratch/cinthiasouza/mv-text-summarizer/notebook/models_features_weights"
embed_path = 'embed_bert'
sections=['introduction', 'materials', 'conclusion', 'concat']
name_models = ['knn', 'ab', 'rf', 'cb', 'gb']

columns = list(range(0, 383))
columns = list(map(str, columns))

predictions_proba, models = load_predict_models(
    dataset, sections, name_models, columns, path_to_save, embed_path, index_Xtest=1)

In [29]:
predictions, predictions_proba, results = ev.create_reports(models, dataset, name_models, index_Xtest=1, index_ytest=3, verbose=False)

# Summarization

In [35]:
"""summ_items = pd.read_csv("indices_summ.csv")['summ']

path = ["../../PMC002xxxxxx_pp", "../../PMC003xxxxxx_pp", "../../PMC005xxxxxx_pp", "../../PMC006xxxxxx_pp"]
references = []
article_name = []
for i in path:
    
    files = os.listdir(i)
    inter = list(set(files) & set(summ_items))
    
    for j in inter:
        references.append(summarization.get_ref_summary(j, i))
        article_name.append(j)
        
references_df = pd.DataFrame({"articles": article_name, 'references': references})

features_intro, scores_intro = loader.read_features(path="../result/introduction/features_*.csv")
features_mat, scores_mat = loader.read_features(path="../result/materials/features_*.csv")
features_conc, scores_conc = loader.read_features(path="../result/conclusion/features_*.csv")"""

In [30]:
summ_items = pd.read_csv("dataset/indices_summ.csv")['summ']

In [31]:
references_df = pd.read_csv("dataset/references_df.csv")

In [32]:
features_intro = pd.read_csv('dataset/dataset_introduction.csv')
features_mat = pd.read_csv('dataset/dataset_materials.csv')
features_conc = pd.read_csv('dataset/dataset_conclusion.csv')

# Abordagem 1

Sumarização utilizando os classificadores

In [33]:
section = 'introduction'

df = dataset[section][5].reset_index(drop=True)
features_intro = df[['sentences', 'articles']]
scores_intro = pd.DataFrame()
scores_intro['rouge_1'] = df['rouge_1']

proba_intro_ex1, df_intro_ex1, summaries_intro_ex1, result_intro_ex1 = pipeline_summarization(
    features_intro, scores_intro, references_df, predictions_proba, section, name_models,
    summ_items, sort_scores=True, proba=True, ascending=False)

In [34]:
section = 'materials'

df = dataset[section][5].reset_index(drop=True)
features_mat = df[['sentences', 'articles']]
scores_mat = pd.DataFrame()
scores_mat['rouge_1'] = df['rouge_1']

proba_mat_ex1, df_mat_ex1, summaries_mat_ex1, result_mat_ex1 = pipeline_summarization(
    features_mat, scores_mat, references_df, predictions_proba, section, name_models,
    summ_items, sort_scores=True, proba=True, ascending=False)

In [35]:
section = 'conclusion'

df = dataset[section][5].reset_index(drop=True)
features_conc = df[['sentences', 'articles']]
scores_conc = pd.DataFrame()
scores_conc['rouge_1'] = df['rouge_1']

df_proba_conc_ex1, df_conc_ex1, summaries_conc_ex1, result_conc_ex1 = pipeline_summarization(
    features_conc, scores_conc, references_df, predictions_proba, section, name_models,
    summ_items, sort_scores=True, proba=True, ascending=False)

In [36]:
section = 'concat'

df = dataset[section][5].reset_index(drop=True)
features_concat = df[['sentences', 'articles']]
scores_concat = pd.DataFrame()
scores_concat['rouge_1'] = df['rouge_1']

df_proba_concat_ex1, df_concat_ex1, summaries_concat_ex1, result_concat_ex1 = pipeline_summarization(
    features_concat, scores_concat, references_df, predictions_proba, section, name_models,
    summ_items, sort_scores=True, proba=True, ascending=False)

In [37]:
summaries_intro_ex1.describe()

knn_r1      knn_r2      knn_rl       ab_r1       ab_r2       ab_rl  \
count  924.000000  924.000000  924.000000  924.000000  924.000000  924.000000   
mean     0.248263    0.090461    0.164508    0.260559    0.099155    0.173199   
std      0.085450    0.060613    0.064995    0.085155    0.061735    0.065026   
min      0.040201    0.000000    0.025210    0.021739    0.000000    0.021739   
25%      0.190744    0.048485    0.122112    0.202615    0.056429    0.129241   
50%      0.240964    0.079470    0.154614    0.253398    0.087575    0.164942   
75%      0.303623    0.122874    0.197229    0.317494    0.134100    0.207573   
max      0.676259    0.554745    0.633094    0.575540    0.423358    0.561151   

            rf_r1       rf_r2       rf_rl       cb_r1       cb_r2       cb_rl  \
count  924.000000  924.000000  924.000000  924.000000  924.000000  924.000000   
mean     0.272815    0.099868    0.174456    0.270134    0.099427    0.173350   
std      0.084224    0.062425    0.065262    0.082818    0.061504    0.063701   
min      0.023669    0.000000    0.023669    0.023669    0.000000    0.023669   
25%      0.214547    0.057637    0.131368    0.213592    0.057319    0.129575   
50%      0.269430    0.088643    0.165713    0.265953    0.088106    0.165713   
75%      0.326531    0.133333    0.206582    0.326198    0.133955    0.204770   
max      0.630872    0.503401    0.604027    0.630872    0.503401    0.604027   

            gb_r1       gb_r2       gb_rl  
count  924.000000  924.000000  924.000000  
mean     0.265524    0.100821    0.175365  
std      0.084544    0.063057    0.065680  
min      0.021739    0.000000    0.021739  
25%      0.209215    0.059172    0.131531  
50%      0.259184    0.088357    0.165632  
75%      0.319726    0.137025    0.210673  
max      0.603448    0.423729    0.561151

In [38]:
summaries_mat_ex1.describe()

knn_r1      knn_r2      knn_rl       ab_r1       ab_r2       ab_rl  \
count  924.000000  924.000000  924.000000  924.000000  924.000000  924.000000   
mean     0.196997    0.087362    0.145488    0.206729    0.094632    0.152875   
std      0.128662    0.130602    0.123654    0.131315    0.132022    0.125689   
min      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
25%      0.115181    0.016327    0.077922    0.117647    0.018692    0.078597   
50%      0.173119    0.043956    0.114468    0.180673    0.050901    0.120982   
75%      0.237850    0.090090    0.163522    0.254545    0.100000    0.169697   
max      0.839161    0.836879    0.839161    0.818182    0.815385    0.818182   

            rf_r1       rf_r2       rf_rl       cb_r1       cb_r2       cb_rl  \
count  924.000000  924.000000  924.000000  924.000000  924.000000  924.000000   
mean     0.207957    0.085868    0.145014    0.199047    0.078085    0.135495   
std      0.121687    0.116112    0.111286    0.118583    0.109989    0.104607   
min      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
25%      0.124823    0.019494    0.080000    0.120000    0.017392    0.075811   
50%      0.188373    0.049597    0.121009    0.176751    0.043384    0.112255   
75%      0.259854    0.097790    0.167397    0.248986    0.091574    0.157068   
max      0.818182    0.815385    0.818182    0.818182    0.815385    0.818182   

            gb_r1       gb_r2       gb_rl  
count  924.000000  924.000000  924.000000  
mean     0.209230    0.096538    0.154887  
std      0.132150    0.133711    0.127096  
min      0.000000    0.000000    0.000000  
25%      0.120000    0.019608    0.081633  
50%      0.186791    0.051580    0.120784  
75%      0.261367    0.104441    0.174523  
max      0.836601    0.834437    0.836601

In [39]:
summaries_conc_ex1.describe()

knn_r1      knn_r2      knn_rl       ab_r1       ab_r2       ab_rl  \
count  924.000000  924.000000  924.000000  924.000000  924.000000  924.000000   
mean     0.258048    0.116434    0.181726    0.272973    0.126031    0.194148   
std      0.106050    0.110981    0.100865    0.115143    0.123009    0.112112   
min      0.026316    0.000000    0.018349    0.024845    0.000000    0.018018   
25%      0.183389    0.041940    0.116867    0.195332    0.044593    0.121920   
50%      0.250000    0.084622    0.160000    0.258199    0.088512    0.167787   
75%      0.310787    0.144058    0.211313    0.335782    0.165574    0.228487   
max      0.779412    0.746269    0.750000    0.840580    0.823529    0.840580   

            rf_r1       rf_r2       rf_rl       cb_r1       cb_r2       cb_rl  \
count  924.000000  924.000000  924.000000  924.000000  924.000000  924.000000   
mean     0.283241    0.119630    0.190890    0.285903    0.117141    0.188150   
std      0.103959    0.105691    0.096716    0.107070    0.103023    0.095027   
min      0.038462    0.000000    0.016529    0.036036    0.000000    0.018018   
25%      0.212847    0.050367    0.129475    0.213775    0.048102    0.124878   
50%      0.271396    0.091326    0.167858    0.273054    0.089536    0.167615   
75%      0.342564    0.152819    0.225352    0.346892    0.152480    0.222222   
max      0.712446    0.709957    0.712446    0.806122    0.731959    0.775510   

            gb_r1       gb_r2       gb_rl  
count  924.000000  924.000000  924.000000  
mean     0.273387    0.128947    0.196785  
std      0.115484    0.125900    0.113795  
min      0.038462    0.000000    0.016529  
25%      0.198861    0.046512    0.123486  
50%      0.261526    0.090206    0.167703  
75%      0.333333    0.158425    0.231494  
max      0.779412    0.746667    0.750000

### Combine

In [77]:
summaries_comb_ex1 = summarization.combine_three_summ(summaries_intro_ex1, summaries_mat_ex1, summaries_conc_ex1, references_df, name_models)

In [78]:
result_comb_ex1 = summarization.evaluate_summaries(summaries_comb_ex1, name_models)

In [79]:
result_comb_ex1.describe()

knn_r1      knn_r2      knn_rl       ab_r1       ab_r2       ab_rl  \
count  924.000000  924.000000  924.000000  924.000000  924.000000  924.000000   
mean     0.355288    0.149000    0.208486    0.361006    0.155018    0.211467   
std      0.091146    0.090664    0.074529    0.094971    0.096878    0.080229   
min      0.101493    0.000000    0.047761    0.119266    0.000000    0.055046   
25%      0.292021    0.083644    0.153691    0.293562    0.085329    0.154969   
50%      0.347288    0.128291    0.193649    0.354839    0.131620    0.192026   
75%      0.417769    0.198915    0.250953    0.422243    0.201655    0.250187   
max      0.675462    0.522449    0.489796    0.669145    0.536585    0.535316   

            rf_r1       rf_r2       rf_rl       cb_r1       cb_r2       cb_rl  \
count  924.000000  924.000000  924.000000  924.000000  924.000000  924.000000   
mean     0.361530    0.153278    0.211375    0.362308    0.154665    0.212664   
std      0.092365    0.095179    0.079235    0.093785    0.097911    0.081478   
min      0.082458    0.007117    0.045271    0.113990    0.009852    0.056180   
25%      0.296296    0.084086    0.156012    0.295089    0.083650    0.155725   
50%      0.353818    0.132890    0.193441    0.352000    0.129712    0.193293   
75%      0.423641    0.198383    0.248007    0.425000    0.198886    0.249333   
max      0.668896    0.494253    0.513834    0.679537    0.524476    0.555985   

            gb_r1       gb_r2       gb_rl  
count  924.000000  924.000000  924.000000  
mean     0.361921    0.157032    0.213200  
std      0.094965    0.098463    0.079755  
min      0.104110    0.000000    0.054795  
25%      0.290643    0.084211    0.154519  
50%      0.355929    0.132209    0.198688  
75%      0.425943    0.207311    0.252472  
max      0.702875    0.519878    0.530351

# Abordagem 2

Max Rouge Scores

In [25]:
df_intro_ex2, summaries_intro_ex2, result_intro_ex2 = summarization_target(
    df_intro_ex1, references_df, ['max_rouge'], summ_items, sort_scores=True, proba=True, ascending=False)

In [26]:
df_mat_ex2, summaries_mat_ex2, result_mat_ex2 = summarization_target(
    df_mat_ex1, references_df, ['max_rouge'], summ_items, sort_scores=True, proba=True, ascending=False)

In [27]:
df_conc_ex2, summaries_conc_ex2, result_conc_ex = summarization_target(
    df_conc_ex1.copy(), references_df, ['max_rouge'], summ_items, sort_scores=True, proba=True, ascending=False)

In [28]:
summaries_intro_ex2.describe()

max_rouge_r1  max_rouge_r2  max_rouge_rl
count    171.000000    171.000000    171.000000
mean       0.315888      0.149282      0.219503
std        0.080887      0.069231      0.073439
min        0.140625      0.026490      0.091503
25%        0.257386      0.102010      0.173296
50%        0.307692      0.139194      0.207207
75%        0.363105      0.188111      0.259041
max        0.630872      0.503401      0.604027

In [29]:
summaries_mat_ex2.describe()

max_rouge_r1  max_rouge_r2  max_rouge_rl
count    171.000000    171.000000    171.000000
mean       0.283041      0.161399      0.222057
std        0.159187      0.185150      0.171321
min        0.048485      0.000000      0.037975
25%        0.174458      0.045584      0.115656
50%        0.244604      0.090226      0.161943
75%        0.349084      0.172650      0.254187
max        0.793651      0.790323      0.793651

In [30]:
summaries_conc_ex2.describe()

max_rouge_r1  max_rouge_r2  max_rouge_rl
count    171.000000    171.000000    171.000000
mean       0.338445      0.205545      0.262925
std        0.132557      0.169658      0.150835
min        0.038462      0.000000      0.038462
25%        0.249088      0.081279      0.154971
50%        0.314815      0.136364      0.220588
75%        0.402703      0.270837      0.320095
max        0.854167      0.852632      0.854167

# Combine

In [31]:
summaries_comb_ex2 = summarization.combine_three_summ(summaries_intro_ex2, summaries_mat_ex2, summaries_conc_ex2, references_df, ['max_rouge'])
result_comb_ex2 = summarization.evaluate_summaries(summaries_comb_ex2, ['max_rouge'])

In [32]:
result_comb_ex2.describe()

max_rouge_r1  max_rouge_r2  max_rouge_rl
count    171.000000    171.000000    171.000000
mean       0.504175      0.295633      0.341743
std        0.108762      0.140313      0.125709
min        0.258065      0.066667      0.121212
25%        0.421803      0.180140      0.239541
50%        0.505338      0.272000      0.315789
75%        0.577073      0.407645      0.429475
max        0.785992      0.698039      0.739300

# Abordagem 3 

Min ROUGE scores

In [79]:
df_intro_ex3, summaries_intro_ex3, result_intro_ex3 = summarization_target(
    df_intro_ex1, references_df, ['min_rouge'], summ_items, sort_scores=True, proba=True, ascending=True)

In [82]:
df_mat_ex3, summaries_mat_ex3, result_mat_ex3 = summarization_target(
    df_mat_ex1.copy(), references_df, ['min_rouge'], summ_items, sort_scores=True, proba=True, ascending=True)

In [83]:
df_conc_ex3, summaries_conc_ex3, result_conc_ex3 = summarization_target(
    df_conc_ex1.copy(), references_df, ['min_rouge'], summ_items, sort_scores=True, proba=True, ascending=True)

In [81]:
summaries_intro_ex3.describe()

min_rouge_r1  min_rouge_r2  min_rouge_rl
count    171.000000    171.000000    171.000000
mean       0.066270      0.008626      0.045411
std        0.052096      0.018103      0.031295
min        0.000000      0.000000      0.000000
25%        0.031414      0.000000      0.023906
50%        0.060302      0.000000      0.041379
75%        0.087485      0.011495      0.058323
max        0.315789      0.144928      0.172249

In [85]:
summaries_mat_ex3.describe()

min_rouge_r1  min_rouge_r2  min_rouge_rl
count    171.000000    171.000000    171.000000
mean       0.030388      0.007367      0.023757
std        0.059538      0.043516      0.049944
min        0.000000      0.000000      0.000000
25%        0.000000      0.000000      0.000000
50%        0.011111      0.000000      0.011111
75%        0.037431      0.000000      0.031873
max        0.443515      0.430380      0.443515

In [84]:
summaries_conc_ex3.describe()

min_rouge_r1  min_rouge_r2  min_rouge_rl
count    171.000000    171.000000    171.000000
mean       0.050444      0.006450      0.032716
std        0.063669      0.016958      0.038023
min        0.000000      0.000000      0.000000
25%        0.000000      0.000000      0.000000
50%        0.029851      0.000000      0.021858
75%        0.083333      0.000000      0.051460
max        0.358744      0.117647      0.180328

## Combine

In [86]:
summaries_comb_ex3 = summarization.combine_three_summ(summaries_intro_ex3, summaries_mat_ex3, summaries_conc_ex3, references_df, ['min_rouge'])
result_comb_ex3 = summarization.evaluate_summaries(summaries_comb_ex3, ['min_rouge'])

In [87]:
result_comb_ex3.describe()

min_rouge_r1  min_rouge_r2  min_rouge_rl
count    171.000000    171.000000    171.000000
mean       0.100364      0.015847      0.059637
std        0.067647      0.037432      0.041306
min        0.000000      0.000000      0.000000
25%        0.050162      0.000000      0.034263
50%        0.086124      0.006431      0.054422
75%        0.129771      0.017701      0.074617
max        0.418919      0.353741      0.358108

# Abordagem 4

3 primeiras sentenças de cada seção

In [125]:
df_intro_ex4, summaries_intro_ex4, result_intro_ex4 = summarization_target(
    df_intro_ex1.copy(), references_df, ['first_three'], summ_items, sort_scores=False, proba=False, ascending=True)

In [127]:
df_mat_ex4, summaries_mat_ex4, result_mat_ex4 = summarization_target(
    df_mat_ex1.copy(), references_df, ['first_three'], summ_items, sort_scores=False, proba=False, ascending=True)

In [128]:
df_conc_ex4, summaries_conc_ex4, result_conc_ex4 = summarization_target(
    df_conc_ex1.copy(), references_df, ['first_three'], summ_items, sort_scores=False, proba=False, ascending=True)

In [129]:
summaries_intro_ex4.describe()

first_three_r1  first_three_r2  first_three_rl
count      171.000000      171.000000      171.000000
mean         0.151015        0.050389        0.106543
std          0.074139        0.047770        0.054121
min          0.000000        0.000000        0.000000
25%          0.097760        0.018391        0.068966
50%          0.142077        0.035714        0.095890
75%          0.194335        0.067091        0.136054
max          0.402010        0.274112        0.361809

In [130]:
summaries_mat_ex4.describe()

first_three_r1  first_three_r2  first_three_rl
count      171.000000      171.000000      171.000000
mean         0.144131        0.051007        0.104438
std          0.088074        0.070782        0.072574
min          0.000000        0.000000        0.000000
25%          0.080312        0.011872        0.059174
50%          0.128440        0.030457        0.089385
75%          0.184450        0.061072        0.125000
max          0.517007        0.510345        0.517007

In [131]:
summaries_conc_ex4.describe()

first_three_r1  first_three_r2  first_three_rl
count      171.000000      171.000000      171.000000
mean         0.214064        0.073632        0.144273
std          0.095354        0.059381        0.067457
min          0.000000        0.000000        0.000000
25%          0.146175        0.025409        0.097222
50%          0.217391        0.063158        0.139241
75%          0.274977        0.100784        0.184921
max          0.454545        0.284404        0.389262

## Combine

In [132]:
summaries_comb_ex4 = summarization.combine_three_summ(summaries_intro_ex4, summaries_mat_ex4, summaries_conc_ex4, references_df, ['first_three'])
result_comb_ex4 = summarization.evaluate_summaries(summaries_comb_ex4, ['first_three'])

In [133]:
result_comb_ex4.describe()

first_three_r1  first_three_r2  first_three_rl
count      171.000000      171.000000      171.000000
mean         0.297858        0.107031        0.175054
std          0.086220        0.066728        0.061321
min          0.100000        0.004367        0.045872
25%          0.230654        0.059457        0.131755
50%          0.298755        0.096491        0.167224
75%          0.357676        0.139099        0.205166
max          0.550633        0.351351        0.392857

# Summary

In [96]:
result_comb_ex1.describe()

knn_r1      knn_r2      knn_rl       rf_r1       rf_r2       rf_rl  \
count  171.000000  171.000000  171.000000  171.000000  171.000000  171.000000   
mean     0.389468    0.182206    0.235748    0.375271    0.167637    0.221202   
std      0.092970    0.101906    0.083162    0.100695    0.095609    0.084530   
min      0.190083    0.016667    0.098039    0.111570    0.008299    0.049587   
25%      0.319147    0.104818    0.178848    0.299501    0.098072    0.158480   
50%      0.384401    0.163793    0.222222    0.368852    0.142857    0.203008   
75%      0.454601    0.237712    0.279241    0.440786    0.215818    0.274393   
max      0.648318    0.530806    0.544601    0.634615    0.506550    0.502165   

            cb_r1       cb_r2       cb_rl       gb_r1       gb_r2       gb_rl  \
count  171.000000  171.000000  171.000000  171.000000  171.000000  171.000000   
mean     0.390841    0.174419    0.233853    0.397058    0.186601    0.242635   
std      0.088876    0.092109    0.077968    0.094541    0.100552    0.084104   
min      0.110169    0.008511    0.050847    0.185484    0.016260    0.088710   
25%      0.325673    0.108108    0.175219    0.322484    0.112668    0.182545   
50%      0.393443    0.150000    0.222222    0.402778    0.167401    0.227405   
75%      0.449655    0.234385    0.281899    0.471901    0.245927    0.297332   
max      0.620690    0.441640    0.445141    0.595469    0.450704    0.475309   

           mlp_r1      mlp_r2      mlp_rl  
count  171.000000  171.000000  171.000000  
mean     0.364408    0.155399    0.218202  
std      0.092586    0.093350    0.083592  
min      0.164654    0.024096    0.088889  
25%      0.303754    0.086559    0.161457  
50%      0.356808    0.143284    0.202020  
75%      0.423729    0.196239    0.258246  
max      0.645570    0.556098    0.560386

In [97]:
result = pd.concat([result_comb_ex2.describe(), result_comb_ex3.describe() ,result_comb_ex4.describe()], axis=1)
result

max_rouge_r1  max_rouge_r2  max_rouge_rl  min_rouge_r1  min_rouge_r2  \
count    171.000000    171.000000    171.000000    171.000000    171.000000   
mean       0.504175      0.295633      0.341743      0.100364      0.015847   
std        0.108762      0.140313      0.125709      0.067647      0.037432   
min        0.258065      0.066667      0.121212      0.000000      0.000000   
25%        0.421803      0.180140      0.239541      0.050162      0.000000   
50%        0.505338      0.272000      0.315789      0.086124      0.006431   
75%        0.577073      0.407645      0.429475      0.129771      0.017701   
max        0.785992      0.698039      0.739300      0.418919      0.353741   

       min_rouge_rl  first_three_r1  first_three_r2  first_three_rl  
count    171.000000      171.000000      171.000000      171.000000  
mean       0.059637        0.297858        0.107031        0.175054  
std        0.041306        0.086220        0.066728        0.061321  
min        0.000000        0.100000        0.004367        0.045872  
25%        0.034263        0.230654        0.059457        0.131755  
50%        0.054422        0.298755        0.096491        0.167224  
75%        0.074617        0.357676        0.139099        0.205166  
max        0.358108        0.550633        0.351351        0.392857

## Experimento 1

Objetivo: analisar a distribuição entre os scores das métricas rouge entre os resumos candidatos e os resumos referência

1. Crio um resumo composto por 3 sentenças de cada seção;
2. Comparo esse resumo com o resumo referencia. 


In [98]:
import plotly.graph_objects as go
import numpy as np

In [102]:
def plot_hist_rouge_sent(df, title):

    fig = go.Figure()

    for i in df.columns:
        fig.add_trace(go.Histogram(x=df[i], name=i))


    fig.update_layout(barmode='overlay', title=title)
    fig.show()

In [275]:
aux = pd.DataFrame()

aux['Max']= result_comb_ex2['max_rouge_r1']
aux['Min']= result_comb_ex3['min_rouge_r1']
aux['first_three']= result_comb_ex4['first_three_r1']
aux['KNN']= result_comb_ex1['knn_r1']
aux['AB']= result_comb_ex1['ab_r1']
aux['RF']= result_comb_ex1['rf_r1']
aux['CB']= result_comb_ex1['cb_r1']
aux['GB']= result_comb_ex1['gb_r1']
aux['MLP']= result_comb_ex1['mlp_r1']
aux['MV_MLP']= result_comb_ex1['mv_mlp_bert_r1']

plot_hist_rouge_sent(aux, title="Distribuição dos scores de rouge-1 dos resumos candidatos")

In [276]:
aux = pd.DataFrame()

aux['Max']= result_comb_ex2['max_rouge_r2']
aux['Min']= result_comb_ex3['min_rouge_r2']
aux['first_three']= result_comb_ex4['first_three_r2']
aux['KNN']= result_comb_ex1['knn_r2']
#aux['AB']= result_comb_ex1['ab_r1'2]
aux['RF']= result_comb_ex1['rf_r2']
aux['CB']= result_comb_ex1['cb_r2']
aux['GB']= result_comb_ex1['gb_r2']
aux['MLP']= result_comb_ex1['mlp_r2']
aux['MV_MLP']= result_comb_ex1['mv_mlp_bert_r1']


plot_hist_rouge_sent(aux, title="Distribuição dos scores de rouge-2 dos resumos candidatos")

# Experimento 2

Objetivo: Verificar se existe alguma diferença na distribuição de scores das sentenças selecionadas pela abordagem q seleciona as 3 primeiras sentenças e os algoritmos de classificação?


1. Crio um resumo composto por 3 sentenças de cada seção;
2. Comparo esse resumo com o resumo referencia. 


Ap 1 - Selecionou as sentenças 9 sentenças, 3 de cada seção. 
Ap 2 - Selecionou as sentenças 9 sentenças, 3 de cada seção.

Comparamos os resumos de Ap 1 e 2 com o resumo candidato. Os scores obtidos estão sendo apresentados nas figuras.


In [104]:
import plotly.graph_objects as go
import numpy as np

def plot_dist_rouge_sent(df, title, box_visible=False):

    fig = go.Figure()

    for i in df.columns:
        fig.add_trace(go.Violin(y=df[i], name=i, box_visible=box_visible, meanline_visible=True))

    fig.update_traces(orientation='v')
    fig.update_layout(title_text=title)
    fig.show()


In [277]:
r1_plot = pd.DataFrame()

r1_plot['max_rouge']= result_comb_ex2['max_rouge_r1']
r1_plot['min_rouge'] = result_comb_ex3['min_rouge_r1']
r1_plot['first_three'] = result_comb_ex4['first_three_r1']
r1_plot['KNN']= result_comb_ex1['knn_r1']
aux['AB']= result_comb_ex1['ab_r1']
r1_plot['RF']= result_comb_ex1['rf_r1']
r1_plot['CB']= result_comb_ex1['cb_r1']
r1_plot['GB']= result_comb_ex1['gb_r1']
r1_plot['MLP']= result_comb_ex1['mlp_r1']
aux['MV_MLP']= result_comb_ex1['mv_mlp_bert_r1']


plot_dist_rouge_sent(r1_plot, title="Distribuição dos scores de rouge-1 dos resumos gerados", box_visible=True)

In [278]:
r2_plot = pd.DataFrame()

r2_plot['max_rouge']= result_comb_ex2['max_rouge_r2']
r2_plot['min_rouge'] = result_comb_ex3['min_rouge_r2']
r2_plot['first_three'] = result_comb_ex4['first_three_r2']
r2_plot['KNN']= result_comb_ex1['knn_r2']
#aux['AB']= result_comb_ex1['ab_r1'2]
r2_plot['RF']= result_comb_ex1['rf_r2']
r2_plot['CB']= result_comb_ex1['cb_r2']
r2_plot['GB']= result_comb_ex1['gb_r2']
r2_plot['MLP']= result_comb_ex1['mlp_r2']
aux['MV_MLP']= result_comb_ex1['mv_mlp_bert_r2']



plot_dist_rouge_sent(r2_plot, title="Distribuição dos scores de rouge-2 dos resumos gerados", box_visible=True)

# Experimento 3

Objetivo: Verificar a distribuição dos scores de rouge-1 das sentenças selecionadas pelos algoritmos e pela abordagem que seleciona as três primeiras sentenças. 

Quero ver se realmente as médias dos scores são iguais pois as sentenças seleciodas possuem scores semelhantes ou se ao combinar as sentenças os resumos obtiveram scores semelhantes.

1. Seleciono três sentenças de cada seção
2. Seleciono o rótulo dessas sentenças e avalio a distribuição.


Obs. O rótulo da sentença é o max do score de rouge-1 da sentença com todas as sentenças do resumo referência.



In [279]:
def get_label_sentences(df, df_ex2, df_ex4, name_models):
    
    label = pd.DataFrame()
    
    label['max_rouge'] = df_ex2.loc[df_ex2['max_rouge'] == 1 ]['rouge_1'].reset_index(drop=True)
    label['first_three']  = df_ex4.loc[df_ex4['first_three'] == 1 ]['rouge_1'].reset_index(drop=True)
    
    for i in name_models:
        label[i] = df.loc[df[i] == 1 ]['rouge_1'].reset_index(drop=True)
        
    return label

In [280]:
label_intro = get_label_sentences(df_intro_ex1, df_intro_ex2, df_intro_ex4, name_models=['knn', 'ab', 'rf', 'cb', 'gb', 'mlp', 'mv_mlp_bert'])
plot_dist_rouge_sent(label_intro, box_visible=True, title="Distribuição dos score max de rouge-1 entre as sentenças selecionadas e o resumo de referência")
                                                           

In [281]:
def plot_bar(df, names, title):

    fig = go.Figure()
    
    for i in df.columns:
        fig.add_trace(go.Bar(name=i, x=names, y=df[i]))
        
    fig.update_layout(barmode='stack',title_text=title)
    fig.show()

In [282]:
def compare_models_scores(label, name_models):
    
    test = pd.DataFrame()
    
    for i in name_models:

        test['{}_gt_ft'.format(i)] =  label[i] > label.first_three 
        test['{}_gt_ft'.format(i)] = test['{}_gt_ft'.format(i)].astype(int)
        test['{}_lt_ft'.format(i)] =  label[i] < label.first_three 
        test['{}_lt_ft'.format(i)] =test['{}_lt_ft'.format(i)].astype(int)
        test['{}_eq_ft'.format(i)] = label.first_three == label[i]
        test['{}_eq_ft'.format(i)]=test['{}_eq_ft'.format(i)].astype(int)
        
    
    count = test.apply(pd.value_counts)
    count = count.drop(0, axis=0)    
    
    df_count = pd.DataFrame()
    
    gt = []
    lt = []
    eq = []

    for i in count.columns:

        if i.find('gt') != -1:
            gt.append(int(count[i]))
        elif i.find('lt') != -1:
            lt.append(int(count[i]))
        elif i.find('eq') != -1:
            eq.append(int(count[i]))

    df_count['gt'] = gt
    df_count['lt'] = lt
    df_count['eq'] = eq
        
    return df_count


In [283]:
test = compare_models_scores(label_intro, name_models=['knn', 'ab', 'rf', 'cb', 'gb', 'mlp', 'mv_mlp_bert'])

names =['knn', 'ab', 'rf', 'cb', 'gb', 'mlp', 'mv_mlp_bert']

plot_bar(test, names, 'Análise dos scores de ROUGE-1 das sentenças selecionadas - Introdução')

In [284]:
label_mat = get_label_sentences(df_mat_ex1, df_mat_ex2, df_mat_ex4, name_models=['knn', 'ab', 'rf', 'cb', 'gb', 'mlp', 'mv_mlp_bert'])
plot_dist_rouge_sent(label_mat, box_visible=True, title="Distribuição dos score max de rouge-1 entre as sentenças selecionadas e o resumo de referência")
                     

In [285]:
test = compare_models_scores(label_mat, name_models=['knn', 'ab', 'rf', 'cb', 'gb', 'mlp', 'mv_mlp_bert'])

plot_bar(test, names, 'Análise dos scores de ROUGE-1 das sentenças selecionadas - Materiais e Métodos')

In [286]:
label_conc = get_label_sentences(df_conc_ex1, df_conc_ex2, df_conc_ex4, name_models=['knn', 'ab', 'rf', 'cb', 'gb', 'mlp', 'mv_mlp_bert'])
plot_dist_rouge_sent(label_conc, box_visible=True, title="Distribuição dos score max de rouge-1 entre as sentenças selecionadas e o resumo de referência")
   

In [287]:
test = compare_models_scores(label_conc, name_models=['knn', 'ab', 'rf', 'cb', 'gb', 'mlp', 'mv_mlp_bert'])
plot_bar(test, names, 'Análise dos scores de ROUGE-1 das sentenças selecionadas - Conclusão')

# Experimento 8

Objetivo: Identificar tendência posicionais na seleção de sentenças.

1. Seleciono três sentenças de cada seção;
2. Categorizo as sentenças em três classes:
    Begin: posição 0, 1, 2
    End: posição num(sentenças)-0,num(sentenças)-1, num(sentenças)-2

In [150]:
def get_positions(df, column_name):

    positions = []
    length = []
    
    for i in summ_items:

        aux = df.loc[ df['articles'] == i].reset_index(drop= True)
        length.append(aux.shape[0])
        positions.append(aux.loc[aux[column_name] == 1].index.tolist())
        
    return positions, length

In [317]:
def count_positions(df, column_name, new_column):
    j = 0
    aux = []
    
    positions, length = get_positions(df, column_name)

    for position in positions:
        for i in position:

            if (i == 0) or (i<4):
                aux.append("begin")
            elif (i == length[j]) or (i <= (length[j]-2)):
                aux.append('end')
            else:
                aux.append('middle')

        j+=1

    count_positions = pd.DataFrame(Counter(aux), index=[new_column]).T.reset_index()
    

    return count_positions

In [321]:
def count_all_sections(df_intro, df_mat, df_conc, column_name):

    count_intro = count_positions(df_intro, column_name=column_name, new_column='count_intro')
    count_mat = count_positions(df_mat, column_name=column_name, new_column='count_mat')
    count_conc = count_positions(df_conc, column_name=column_name, new_column='count_conc')

    aux = count_intro.merge(count_mat, on='index')
    aux = aux.merge(count_conc, on='index')
    
    aux = aux.set_index('index').T
    
    res = aux.div(aux.sum(axis=1), axis=0)*100
    
    return aux, res

In [153]:
name_sections=['introduction', 'materials', 'conclusion']

In [319]:
count_ex1_knn, res_ex1_knn = count_all_sections(df_intro_ex1, df_mat_ex1, df_conc_ex1, column_name='knn')
plot_bar(res_ex1_knn[['end', 'middle', 'begin']], name_sections, title='Localização das 3 sentenças com maior probabilidade - KNN')

In [322]:
count_ex1_rf, res_ex1_rf = count_all_sections(df_intro_ex1, df_mat_ex1, df_conc_ex1, column_name='rf')
plot_bar(res_ex1_rf[['end', 'middle', 'begin']], name_sections, title='Localização das 3 sentenças com maior probabilidade - Random Forest')

In [323]:
count_ex1_cb, res_ex1_cb = count_all_sections(df_intro_ex1, df_mat_ex1, df_conc_ex1, column_name='cb')
plot_bar(res_ex1_cb[['end', 'middle', 'begin']], name_sections, title='Localização das 3 sentenças com maior probabilidade - CatBoost')

In [324]:
count_ex1_gb, res_ex1_gb = count_all_sections(df_intro_ex1, df_mat_ex1, df_conc_ex1, column_name='gb')
plot_bar(res_ex1_gb[['end', 'middle', 'begin']], name_sections, title='Localização das 3 sentenças com maior probabilidade - Gradient Boost')

In [325]:
count_ex1_mlp,res_ex1_mlp = count_all_sections(df_intro_ex1, df_mat_ex1, df_conc_ex1, column_name='mlp')
plot_bar(res_ex1_mlp[['end', 'middle', 'begin']], name_sections, title='Localização das 3 sentenças com maior probabilidade - MLP')

In [326]:
count_ex1_mvmlp, res_ex1_mvmlp = count_all_sections(df_intro_ex1, df_mat_ex1, df_conc_ex1, column_name='mv_mlp_bert')
plot_bar(res_ex1_mvmlp[['end', 'middle', 'begin']], name_sections, title='Localização das 3 sentenças com maior probabilidade - MV MLP')

In [327]:
count_ex2, res_ex2 = count_all_sections(df_intro_ex2, df_mat_ex2, df_conc_ex2, column_name='max_rouge')
plot_bar(res_ex2[['end', 'middle', 'begin']], name_sections, title='Localização das 3 sentenças de maior score por seção')

In [162]:
import plotly.graph_objects as go

import pandas as pd

fig = go.Figure()

x_intro = ['Introduction'] * len(summaries_intro_ex1['mlp_r1'])
x_mat = ['Materials'] * len(summaries_mat_ex1['mlp_r1'])
x_conc = ['Conclusion'] * len(summaries_conc_ex1['mlp_r1'])

fig.add_trace(go.Violin(x = x_intro, y=summaries_intro_ex1['rf_r1'], name='AP1',
                        side='negative'))
             
fig.add_trace(go.Violin(x = x_intro, y=summaries_intro_ex4['first_three_r1'], name='AP4',
                        side='positive'))

fig.add_trace(go.Violin(x = x_mat, y=summaries_mat_ex1['rf_r1'], name='AP1',
                        side='negative'))
             
fig.add_trace(go.Violin(x = x_mat, y=summaries_mat_ex4['first_three_r1'], name='AP4',
                        side='positive'))

fig.add_trace(go.Violin(x = x_conc, y=summaries_conc_ex1['rf_r1'], name='AP1',
                        side='negative'))
             
fig.add_trace(go.Violin(x = x_conc, y=summaries_conc_ex4['first_three_r1'], name='AP4',
                        side='positive'))
             
             
fig.update_traces(meanline_visible=True, orientation='v')
fig.update_layout( violinmode='overlay')
fig.show()

# Análise do valor de K

In [345]:
def test_parameter_k(
    features, scores, references_df, predictions_proba, section, name_models,
    summ_items, max_value=15, min_value=1, ):

    mean_dict = {}
    summaries_dict = {}

    for i in range(min_value, max_value):

        proba, df, summaries, result = pipeline_summarization(
        features, scores, references_df, predictions_proba, section, name_models,
        summ_items, k=i,  sort_scores=True, proba=True, ascending=False)

        aux_mean = {}
        aux_summ = {}

        for name_model in name_models:

            aux_mean[name_model] = summaries['{}_r1'.format(name_model)].mean()
            aux_summ[name_model] = summaries[name_model]
            print(summaries[name_model])

        mean_dict[i] = aux_mean
        summaries_dict[i] = aux_summ
        
    df_mean = pd.DataFrame(mean_dict).T.reset_index()
    df_summaries = pd.DataFrame(summaries_dict).T.reset_index()
    
    return df_mean, df_summaries

In [ ]:
df_mean_intro, df_summaries_intro = test_parameter_k(
    features_intro, scores_intro, references_df, predictions_proba, 'introduction', name_models, summ_items)

In [177]:
mean_mat, summaries_mat = test_parameter_k(
    features_mat, scores_mat, references_df, predictions_proba, 'materials', name_models, summ_items)

In [178]:
mean_conc, summaries_conc = test_parameter_k(
    features_conc, scores_conc, references_df, predictions_proba, 'conclusion', name_models, summ_items)

In [204]:
import plotly.graph_objects as go

def bar_plot(df, name_models):

    for name_model in name_models:    

        fig = go.Figure()
        fig.add_trace(go.Bar(x=df['index'], y=df[name_model]))
        fig.update_layout(bargap=0.1, title_text=name_model)
        fig.show()

### Introduction

In [224]:
bar_plot(df_mean_intro, ['knn', 'rf', 'cb', 'gb', 'mlp'])

### Materials

In [203]:
df_mean_mat = pd.DataFrame(mean_mat).T.reset_index()
df_summaries_mat = pd.DataFrame(summaries_mat).T.reset_index()

In [205]:
bar_plot(df_mean_mat, ['knn', 'rf', 'cb', 'gb', 'mlp'])

### Conclusion

In [206]:
df_mean_conc = pd.DataFrame(mean_conc).T.reset_index()
df_summaries_conc = pd.DataFrame(summaries_conc).T.reset_index()

In [207]:
bar_plot(df_mean_conc, ['knn', 'rf', 'cb', 'gb', 'mlp'])

### Concat

In [339]:
comb = {}
name_models = ['knn', 'rf', 'cb', 'gb', 'mlp']
for i in name_models:
    
    comb[i] = df_summaries_intro[i] + df_summaries_mat[i] + df_summaries_conc[i]

In [349]:
comb_eval = summarization.evaluate_summaries(comb, name_models)

KeyError: 'references'